In [1]:
import numpy as np
import matplotlib.pyplot as plt
import tensorflow as tf
#tf.enable_v2_behavior()
# Import tensornetwork
import tensornetwork as tn
# Set the backend to tesorflow
# (default is numpy)
tn.set_default_backend("tensorflow")

In [2]:
mnist = tf.keras.datasets.mnist
(x_train, y_train), (x_test, y_test) = mnist.load_data()

# 0-255の値が入っているので、0-1に収まるよう正規化します
x_train, x_test = x_train / 255.0, x_test / 255.0

In [3]:
print(x_train.shape, x_test.shape)

(60000, 28, 28) (10000, 28, 28)


In [4]:
x_vec = []
for i in range(x_train.shape[0]):
    x_vec_ = np.concatenate([x_train[i][j, ::-2*(j%2)+1] for j in range(x_train.shape[1])])
    x_vec.append(x_vec_)
x_train_1d = np.vstack(x_vec)

x_vec = []
for i in range(x_test.shape[0]):
    x_vec_ = np.concatenate([x_test[i][j, ::-2*(j%2)+1] for j in range(x_test.shape[1])])
    x_vec.append(x_vec_)
x_test_1d = np.vstack(x_vec)

In [5]:
x_train_1d.shape

(60000, 784)

In [6]:
np.random.normal(size = (10,))

array([ 0.76496076,  0.03195237,  1.06098459,  0.61420942, -0.60543453,
        0.15319052, -0.12481708,  0.12476933, -0.36287188, -1.09489632])

In [7]:
# Retrieving a component

def block(*dimensions, norm = 1):
    '''Construct a new matrix for the MPS with random numbers from 0 to 1'''
    size = tuple([x for x in dimensions])
    return np.random.normal(loc = norm, scale = 0.5*norm, size = size)

def create_MPS(rank, dim, bond_dim):
    '''Build the MPS tensor'''
    mps = [
        tn.Node( block(dim, bond_dim) )] + \
        [tn.Node( block(bond_dim, dim, bond_dim)) for _ in range(rank-2)] + \
        [tn.Node( block(bond_dim, dim) )
        ]

    #connect edges to build mps
    connected_edges=[]
    conn=mps[0][1]^mps[1][0]
    connected_edges.append(conn)
    for k in range(1,rank-1):
        conn=mps[k][2]^mps[k+1][0]
        connected_edges.append(conn)

    return mps, connected_edges

def create_MPS_labeled(rank, dim, bond_dim):
    '''Build the MPS tensor'''
    half = np.int((rank - 2) / 2)
    norm = 1 / bond_dim
    mps = [
        tn.Node( block(dim, bond_dim, norm=norm) )] + \
        [tn.Node( block(bond_dim, dim, bond_dim, norm = norm)) for _ in range(half)] + \
        [tn.Node( block(bond_dim, label_dim, bond_dim, norm=norm) )] + \
        [tn.Node( block(bond_dim, dim, bond_dim, norm=norm)) for _ in range(half, rank-2)] + \
        [tn.Node( block(bond_dim, dim, norm=norm) )
        ]

    #connect edges to build mps
    connected_edges=[]
    conn=mps[0][1]^mps[1][0]
    connected_edges.append(conn)
    for k in range(1,rank):
        conn=mps[k][2]^mps[k+1][0]
        connected_edges.append(conn)

    return mps, connected_edges


In [8]:
def feature_map(p):
    phi = [1-p, p]
    return phi

def data_tensorize(vec):
    data_tensor = [tn.Node(feature_map(p)) for p in vec]
    return data_tensor

In [9]:
label_len = 1
label_dim = 10
data_len = x_train_1d.shape[1]
rank = data_len
dim = 2
bond_dim = 10
# mps, edges = create_MPS(rank, dim, bond_dim)
mps, edges = create_MPS_labeled(rank, dim, bond_dim)

test_vec = x_train_1d[0]
data_tensor = data_tensorize(test_vec)

edges.append(data_tensor[0][0] ^ mps[0][0])
half_len = np.int(len(data_tensor) / 2)
[edges.append(data_tensor[i][0] ^ mps[i][1]) for i in range(1, half_len)]
[edges.append(data_tensor[i-label_len][0] ^ mps[i][1]) for i in range(half_len + label_len, data_len + label_len)]
for k in reversed(range(len(edges))):
    A = tn.contract(edges[k])
result = A.tensor

In [10]:
print(A.tensor.numpy())
print(A.tensor.numpy().astype("float32"))
print(tf.math.log(A.tensor).numpy())
print(tf.nn.softmax(A.tensor).numpy())

[0.14253008 0.13955262 0.15180184 0.1299333  0.13143476 0.13872346
 0.14216439 0.14165778 0.14106397 0.12852748]
[0.14253008 0.13955262 0.15180184 0.1299333  0.13143477 0.13872346
 0.1421644  0.14165777 0.14106397 0.12852748]
[-1.94820219 -1.96931356 -1.88517931 -2.04073402 -2.02924464 -1.97527279
 -1.95077118 -1.95434115 -1.95854181 -2.05161252]
[0.10037759 0.10007916 0.10131259 0.09912109 0.09927002 0.09999622
 0.10034089 0.10029007 0.10023053 0.09898184]


In [32]:
def block(*dimensions):
    '''Construct a new matrix for the MPS with random numbers from 0 to 1'''
    size = tuple([x for x in dimensions])
    return tf.Variable(
        tf.random.normal(shape=size, dtype=tf.dtypes.float32, mean= 1/ np.max(size), stddev = 0.5 / np.max(size)),
        trainable=True)

def create_blocks(rank, dim, bond_dim, label_dim):
    half = np.int((rank - 2) / 2)
    blocks = [
        block(dim, bond_dim) ] + \
        [ block(bond_dim, dim, bond_dim) for _ in range(half)] + \
        [ block(bond_dim, label_dim, bond_dim) ] + \
        [ block(bond_dim, dim, bond_dim) for _ in range(half, rank-2)] + \
        [ block(bond_dim, dim) 
        ]
    return blocks

def create_MPS_labeled(blocks, rank, dim, bond_dim):
    '''Build the MPS tensor'''
    half = np.int((rank - 2) / 2)
    mps = []
    for b in blocks:
        mps.append(tn.Node(b))

    #connect edges to build mps
    connected_edges=[]
    conn=mps[0][1]^mps[1][0]
    connected_edges.append(conn)
    for k in range(1,rank):
        conn=mps[k][2]^mps[k+1][0]
        connected_edges.append(conn)

    return mps, connected_edges

In [33]:
# Add a channels dimension
x_train_1d = x_train_1d.astype("float32")
x_test_1d = x_test_1d.astype("float32")
train_ds = tf.data.Dataset.from_tensor_slices(
    (x_train_1d, y_train)).shuffle(60000).batch(32)

test_ds = tf.data.Dataset.from_tensor_slices((x_test_1d, y_test)).batch(32)

In [34]:
from tensorflow.keras import Model

class MyModel(Model):
    def __init__(self, input_len, label_num, bond_dim):
        super(MyModel, self).__init__()
        self.label_len = 1
        self.label_dim = label_num
        self.rank = input_len
        self.dim = 2
        self.bond_dim = bond_dim
        self.blocks = create_blocks(self.rank, self.dim, self.bond_dim, self.label_dim)
        self.softmax = tf.keras.layers.Softmax()

    def call(self, inputs):
        def f(input_vec, blocks, rank, dim, bond_dim, label_len):
            mps, edges = create_MPS_labeled(blocks, rank, dim, bond_dim)
            data_tensor = []
            for p in tf.unstack(input_vec):
                data_tensor.append(tn.Node([1-p, p]))
            edges.append(data_tensor[0][0] ^ mps[0][0])
            half_len = np.int(rank / 2)
            [edges.append(data_tensor[i][0] ^ mps[i][1]) for i in range(1, half_len)]
            [edges.append(data_tensor[i-label_len][0] ^ mps[i][1]) \
                 for i in range(half_len + label_len, rank + label_len)]
            for k in reversed(range(len(edges))):
                A = tn.contract(edges[k])
            result = A.tensor - tf.math.reduce_max(A.tensor)
            return self.softmax(result)

        result = tf.vectorized_map(
        lambda vec: f(vec, self.blocks, self.rank, self.dim, self.bond_dim, self.label_len), inputs)
        return result

In [35]:
N = x_train_1d.shape[1]
label_len = 1
label_num = 10
data_len = x_train_1d.shape[1]
rank = data_len
dim = 2
bond_dim = 10

model = MyModel(N, label_num, bond_dim)

In [36]:
loss_object = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=False)

optimizer = tf.keras.optimizers.Adam(learning_rate=1e-4)

In [37]:
train_loss = tf.keras.metrics.Mean(name='train_loss')
train_accuracy = tf.keras.metrics.SparseCategoricalAccuracy(name='train_accuracy')

test_loss = tf.keras.metrics.Mean(name='test_loss')
test_accuracy = tf.keras.metrics.SparseCategoricalAccuracy(name='test_accuracy')

In [38]:
@tf.function
def train_step(images, labels):
    with tf.GradientTape() as tape:
        predictions = model(images, training=True)
        loss = loss_object(labels, predictions)
    gradients = tape.gradient(loss, model.trainable_variables)
    #print('gradients sample:', gradients[0].numpy())
    optimizer.apply_gradients(zip(gradients, model.trainable_variables))

    train_loss(loss)
    train_accuracy(labels, predictions)

In [39]:
@tf.function
def test_step(images, labels):
    # training=False is only needed if there are layers with different
    # behavior during training versus inference (e.g. Dropout).
    predictions = model(images, training=False)
    t_loss = loss_object(labels, predictions)

    test_loss(t_loss)
    test_accuracy(labels, predictions)

In [40]:
EPOCHS = 5
tf.keras.backend.set_floatx('float32')

for epoch in range(EPOCHS):
    # Reset the metrics at the start of the next epoch
    train_loss.reset_states()
    train_accuracy.reset_states()
    test_loss.reset_states()
    test_accuracy.reset_states()

    for images, labels in train_ds:
        train_step(images, labels)

    for test_images, test_labels in test_ds:
        test_step(test_images, test_labels)

    template = 'Epoch {}, Loss: {}, Accuracy: {}, Test Loss: {}, Test Accuracy: {}'
    print(template.format(epoch + 1,
                        train_loss.result(),
                        train_accuracy.result() * 100,
                        test_loss.result(),
                        test_accuracy.result() * 100))

Epoch 1, Loss: 2.102886438369751, Accuracy: 10.055000305175781, Test Loss: 2.1187641620635986, Test Accuracy: 10.279999732971191
Epoch 2, Loss: 2.0671393871307373, Accuracy: 11.126666069030762, Test Loss: 2.302581787109375, Test Accuracy: 13.220000267028809
Epoch 3, Loss: 2.3025543689727783, Accuracy: 13.25333309173584, Test Loss: 2.302581787109375, Test Accuracy: 13.0600004196167
Epoch 4, Loss: 2.3025543689727783, Accuracy: 12.936666488647461, Test Loss: 2.302579402923584, Test Accuracy: 12.75
Epoch 5, Loss: 2.3025529384613037, Accuracy: 12.095000267028809, Test Loss: 2.3025741577148438, Test Accuracy: 11.130000114440918


In [41]:
(image, label) = (x_train_1d[0], y_train[0])
with tf.GradientTape() as tape:
    # training=True is only needed if there are layers with different
    # behavior during training versus inference (e.g. Dropout).
    predictions = model(images, training=True)
    loss = loss_object(labels, predictions)
gradients = tape.gradient(loss, model.trainable_variables)

In [42]:
predictions

<tf.Tensor: shape=(32, 10), dtype=float32, numpy=
array([[0.10000578, 0.09998142, 0.09999865, 0.10000169, 0.10000557,
        0.10000363, 0.09999313, 0.10000619, 0.09999806, 0.10000597],
       [0.1       , 0.1       , 0.1       , 0.1       , 0.1       ,
        0.1       , 0.1       , 0.1       , 0.1       , 0.1       ],
       [0.1       , 0.1       , 0.1       , 0.1       , 0.1       ,
        0.1       , 0.1       , 0.1       , 0.1       , 0.1       ],
       [0.10000041, 0.09999868, 0.0999999 , 0.10000011, 0.10000039,
        0.10000025, 0.09999951, 0.10000044, 0.09999985, 0.10000043],
       [0.1       , 0.1       , 0.1       , 0.1       , 0.1       ,
        0.1       , 0.1       , 0.1       , 0.1       , 0.1       ],
       [0.10000062, 0.09999801, 0.09999986, 0.10000019, 0.1000006 ,
        0.10000039, 0.09999926, 0.10000066, 0.0999998 , 0.10000064],
       [0.10000002, 0.09999996, 0.09999999, 0.10000001, 0.10000002,
        0.10000002, 0.09999999, 0.10000002, 0.09999999, 0.10

In [43]:
gradients

[<tf.Tensor: shape=(2, 10), dtype=float32, numpy=
 array([[-1.8334169e-05, -2.0357715e-05, -1.6582386e-05, -1.7734228e-05,
         -1.7281054e-05, -1.4524335e-05, -1.7004018e-05, -1.6383892e-05,
         -1.4406390e-05, -2.2048260e-05],
        [ 0.0000000e+00,  0.0000000e+00,  0.0000000e+00,  0.0000000e+00,
          0.0000000e+00,  0.0000000e+00,  0.0000000e+00,  0.0000000e+00,
          0.0000000e+00,  0.0000000e+00]], dtype=float32)>,
 <tf.Tensor: shape=(10, 2, 10), dtype=float32, numpy=
 array([[[-9.3391543e-07, -1.0655164e-06, -9.8044598e-07, -9.2530178e-07,
          -1.1860675e-06, -8.7360701e-07, -1.0144677e-06, -1.2763437e-06,
          -1.0523819e-06, -1.2001187e-06],
         [ 0.0000000e+00,  0.0000000e+00,  0.0000000e+00,  0.0000000e+00,
           0.0000000e+00,  0.0000000e+00,  0.0000000e+00,  0.0000000e+00,
           0.0000000e+00,  0.0000000e+00]],
 
        [[-1.0139653e-06, -1.1568465e-06, -1.0644844e-06, -1.0046135e-06,
          -1.2877306e-06, -9.4848764e-07, -

In [44]:
model.blocks

ListWrapper([<tf.Variable 'Variable:0' shape=(2, 10) dtype=float32, numpy=
array([[0.05962477, 0.06473546, 0.14107682, 0.16899301, 0.08273223,
        0.05635307, 0.14061312, 0.05990366, 0.10665089, 0.09433823],
       [0.08997219, 0.14911309, 0.04288324, 0.08743069, 0.01155961,
        0.0296512 , 0.05403715, 0.05534121, 0.12586008, 0.1383655 ]],
      dtype=float32)>, <tf.Variable 'Variable:0' shape=(10, 2, 10) dtype=float32, numpy=
array([[[ 0.11791597,  0.09946498,  0.07207531,  0.11910263,
          0.12966807,  0.12692949,  0.06477931,  0.15785535,
          0.07368934,  0.07229978],
        [ 0.09217223,  0.16346559,  0.06280096,  0.05016693,
          0.01627415,  0.18531337,  0.13853996,  0.04770579,
          0.11252887,  0.12196954]],

       [[ 0.08655319,  0.12337511,  0.17491865,  0.16737662,
          0.0847735 ,  0.13131265,  0.07944608,  0.05120873,
          0.12325826,  0.15350772],
        [ 0.09429443,  0.11274452,  0.13122647,  0.12116451,
          0.06849228,  0